![sqldw_icon.png](https://github.com/microsoft/sql-data-warehouse-samples/raw/master/samples/sqlops/MonitoringScripts/sqldw_icon.png)
## Azure SQL DW Insights
https://github.com/Microsoft/sql-data-warehouse-samples/tree/master/samples/sqlops/MonitoringScripts

#### Documentation
##### [Data_Skew](https://docs.microsoft.com/en-us/azure/sql-data-warehouse/sql-data-warehouse-tables-distribute#troubleshooting-data-skew), [Low_Rowgroup_Quality](https://docs.microsoft.com/en-us/azure/sql-data-warehouse/sql-data-warehouse-memory-optimizations-for-columnstore-compression#how-to-monitor-rowgroup-quality), [Table_Statistics](https://docs.microsoft.com/en-us/azure/sql-data-warehouse/sql-data-warehouse-tables-statistics#updating-statistics), [Github](https://github.com/Microsoft/sql-data-warehouse-samples)

## Impacted Tables

In [1]:
-- data skew -> cmp_rows>1mil, skew >= 10%
-- missing stats -> cmp_rows>1mil, ctl_rows=1000
-- outdated stats -> cmp_rows>1mil, cmp_rows <> ctl_rows (for (cmp_rows-ctl_rows) > 20%)

declare @minRows int=1000000;
declare @minSkewPercent decimal=10.0;
declare @missingStatCtlRowCount int=1000;
declare @CtlCmpRowDifferencePercentageForOutdatedStats decimal=20.0;

with cmp_details as
(
       select tm.object_id, ps.index_id, ps.distribution_id, count(ps.partition_number) [partitions], sum(ps.row_count) cmp_row_count
       from sys.dm_pdw_nodes_db_partition_stats ps
              join sys.pdw_nodes_tables nt on nt.object_id=ps.object_id and ps.distribution_id=nt.distribution_id
              join sys.pdw_table_mappings tm on tm.physical_name=nt.name
       where ps.index_id<2
       group by tm.object_id, ps.index_id, ps.distribution_id
)
, cmp_summary as
(
       select object_id, index_id, sum(cmp_row_count) cmp_row_count
              , (max(cmp_row_count)-min(cmp_row_count)) highest_skew_rows_difference
              , convert(decimal(10,2),((max(cmp_row_count) - min(cmp_row_count))*100.0 / nullif(sum(cmp_row_count),0))) skew_percent
       from cmp_details
       group by object_id, index_id
)
, ctl_summary as
(
       select t.object_id, i.index_id, s.name sch_name, t.name table_name, i.type_desc table_type, dp.distribution_policy_desc distribution_type, count(p.partition_number) [partitions], sum(p.rows) ctl_row_count
       from sys.schemas s
              join sys.tables t on t.schema_id=s.schema_id
              join sys.pdw_table_distribution_properties dp on dp.object_id=t.object_id
              join sys.indexes i on i.object_id=t.object_id and i.index_id<2
              join sys.partitions p on p.object_id=t.object_id and p.index_id=i.index_id
       group by t.object_id, i.index_id, s.name, t.name, i.type_desc, dp.distribution_policy_desc
)
, [all_results] as
(
       select ctl.object_id, ctl.index_id, ctl.sch_name, ctl.table_name, ctl.table_type, ctl.distribution_type, ctl.[partitions]
              , ctl.ctl_row_count, cmp.cmp_row_count, convert(decimal(10,2),(abs(ctl.ctl_row_count - cmp.cmp_row_count)*100.0 / nullif(cmp.cmp_row_count,0))) ctl_cmp_difference_percent
              , cmp.highest_skew_rows_difference, cmp.skew_percent
              , case 
                     when (ctl.ctl_row_count = @missingStatCtlRowCount) then 'missing stats'
                     when ((ctl.ctl_row_count <> cmp.cmp_row_count) and ((abs(ctl.ctl_row_count - cmp.cmp_row_count)*100.0 / nullif(cmp.cmp_row_count,0)) > @CtlCmpRowDifferencePercentageForOutdatedStats)) then 'outdated stats'
                     else null
                end stat_info
              , case when (cmp.skew_percent >= @minSkewPercent) then 'data skew' else null end skew_info
       from ctl_summary ctl
              join cmp_summary cmp on ctl.object_id=cmp.object_id and ctl.index_id=cmp.index_id
)
select *
from [all_results]
where cmp_row_count>@minRows and (stat_info is not null or skew_info is not null)
order by sch_name, table_name

(17 rows affected)

Total execution time: 00:00:04.376

object_id index_id sch_name table_name table_type distribution_type partitions ctl_row_count cmp_row_count ctl_cmp_difference_percent highest_skew_rows_difference skew_percent stat_info skew_info 1109631046 1 dbo Claim11 CLUSTERED COLUMNSTORE HASH 1 1000 30697250 100.00 4293 0.01 missing stats NULL 266640193 1 dbo Claim12 CLUSTERED COLUMNSTORE HASH 1 33271185 33271185 0.00 33004530 99.20 NULL data skew 1429632186 1 dbo Claim12_Old CLUSTERED COLUMNSTORE HASH 1 61394506 61394506 0.00 30700607 50.01 NULL data skew 284580102 1 dbo hashOrganicRAMP CLUSTERED COLUMNSTORE HASH 1 1000 113220791 100.00 27560 0.02 missing stats NULL 478168999 1 dbo ifrsFactorsBMCWpost2015 CLUSTERED COLUMNSTORE HASH 1 1000 12288792 99.99 86496 0.70 missing stats NULL 1719781284 1 dbo Inforce12 CLUSTERED COLUMNSTORE HASH 1 1027364723 1027364723 0.00 342466049 33.33 NULL data skew 1493632414 1 dbo Input12 CLUSTERED COLUMNSTORE HASH 1 256285023 369221192 30.59 34018 0.01 outdated stats NULL 334168486 1 dbo Input12_Dev CLUSTERED COLUMNSTORE HASH 1 1000 256092982 100.00 31211 0.01 missing stats NULL 1593980955 1 dbo LINC11_JEFF01_CCFactors CLUSTERED COLUMNSTORE HASH 1 1000 1046784 99.90 24816 2.37 missing stats NULL 1609981012 1 dbo LINC11_JEFF01_IFRSFactors CLUSTERED COLUMNSTORE HASH 1 1046784 2093568 50.00 49632 2.37 outdated stats NULL 1181963287 1 dbo MI_2019Assumption CLUSTERED COLUMNSTORE ROUND_ROBIN 1 1000 13866640 99.99 12550 0.09 missing stats NULL 991394651 1 dbo output12_A CLUSTERED COLUMNSTORE ROUND_ROBIN 1 400 14371388 100.00 835 0.01 outdated stats NULL 1461632300 1 dbo Premium12_old CLUSTERED COLUMNSTORE HASH 1 317031244 317031244 0.00 158521552 50.00 NULL data skew 612249286 1 dbo RamTestHash CLUSTERED COLUMNSTORE HASH 1 1000 50329620 100.00 150516 0.30 missing stats NULL 303652475 1 dbo summaryDiagnostics CLUSTERED COLUMNSTORE HASH 1 1000 590144818 100.00 102745 0.02 missing stats NULL 234640079 0 dbo T_5360a8c0610142848e65d02db873bac1 HEAP ROUND_ROBIN 1 1000 33271185 100.00 816 0.00 missing stats NULL 282640250 0 dbo T_a8e47c4c97f9414fb5673be090b15337 HEAP ROUND_ROBIN 1 1000 33271185 100.00 945 0.00 missing stats NULL

## Latest Backup

In [2]:
/* Latest backup deatils */
SELECT TOP 1
	start_time									[start_time]
	, end_time									[end_time]
	, progress									[progress_percent]
	, DATEDIFF(SECOND, start_time, end_time)	[duration_seconds]
FROM
	[sys].[pdw_loader_backup_runs]
ORDER BY
	[run_id] DESC;

(1 row affected)

Total execution time: 00:00:00.249

start_time end_time progress_percent duration_seconds 2020-06-01 16:41:37.850 2020-06-01 16:41:57.943 100 20

## Memory Consumption

In [3]:
/*-- sys.dm_pdw_sql_requests with the correct node id
CREATE VIEW sql_requests AS
(SELECT
       sr.request_id,
       sr.step_index,
       (CASE 
              WHEN (sr.distribution_id = -1 ) THEN 
              (SELECT pdw_node_id FROM sys.dm_pdw_nodes WHERE type = 'CONTROL') 
              ELSE d.pdw_node_id END) AS pdw_node_id,
       sr.distribution_id,
       sr.status,
       sr.error_id,
       sr.start_time,
       sr.end_time,
       sr.total_elapsed_time,
       sr.row_count,
       sr.spid,
       sr.command
FROM sys.pdw_distributions AS d
RIGHT JOIN sys.dm_pdw_sql_requests AS sr ON d.distribution_id = sr.distribution_id)
*/

-- Memory consumption
SELECT
  pc1.pdw_node_id,
  pc1.cntr_value * 100.0/pc2.cntr_value AS Memory_Utilization_Percentage
FROM
-- pc1: current memory
sys.dm_pdw_nodes_os_performance_counters AS pc1
-- pc2: total memory allowed for this SQL instance
JOIN sys.dm_pdw_nodes_os_performance_counters AS pc2 
ON pc1.object_name = pc2.object_name AND pc1.pdw_node_id = pc2.pdw_node_id
WHERE
pc1.counter_name = 'Total Server Memory (KB)'
AND pc2.counter_name = 'Target Server Memory (KB)'


(16 rows affected)

Total execution time: 00:00:00.577

pdw_node_id Memory_Utilization_Percentage 49 87.637567940660563 1 88.978586530096906 54 88.012852906750288 6 90.122265753287328 42 88.284116977571155 8 89.645926357671447 38 89.113757693360445 53 89.831142021035157 58 2.333737755089462 48 89.805014071798473 24 89.192462668806338 56 90.041294606889076 23 90.616307663942981 37 87.802212386349020 55 90.198354887446040 10 88.573464790710155

## Memory Grant

In [4]:
/* Calculating memory grants per table */
SELECT schm_name + '.' + table_name AS Table_name
	--,CAST((table_overhead * 1.0 + column_size + short_string_size + long_string_size) AS DECIMAL(18, 2)) AS est_mem_grant_B
	,CAST((table_overhead * 1.0 + column_size + short_string_size + long_string_size) / 1048576 AS DECIMAL(18, 2)) AS est_mem_grant_MiB
	--,CAST((table_overhead * 1.0 + column_size + short_string_size + long_string_size) / 1073741824 AS DECIMAL(18, 2)) AS est_mem_grant_GiB
FROM (
	SELECT schm_name
		,table_name
		,75497472 AS table_overhead
		,column_count * 1048576 * 8 AS column_size
		,short_string_count * 1048576 * 32 AS short_string_size
		,(long_string_count * 16777216) - (32 * long_string_count) AS long_string_size
	FROM (
		SELECT schm_name
			,table_name
			,SUM(CAST(column_count AS BIGINT)) AS column_count
			,ISNULL(SUM(CAST(short_string_count AS BIGINT)), 0) AS short_string_count
			,ISNULL(SUM(CAST(long_string_count AS BIGINT)), 0) AS long_string_count
		FROM (
			SELECT sm.name AS schm_name
				,tb.name AS table_name
				,COUNT(CAST(co.column_id AS BIGINT)) AS column_count
				,CASE 
					WHEN co.system_type_id IN (
							167
							,175
							,231
							,239
							)
						AND co.max_length <= 32
						THEN COUNT(CAST(co.column_id AS BIGINT))
					END AS short_string_count
				,CASE 
					WHEN co.system_type_id IN (
							167
							,175
							,231
							,239
							)
						AND co.max_length > 32
						THEN COUNT(CAST(co.column_id AS BIGINT))
					END AS long_string_count
			FROM sys.schemas AS sm
			INNER JOIN sys.tables AS tb ON sm.[schema_id] = tb.[schema_id]
			INNER JOIN sys.columns AS co ON tb.[object_id] = co.[object_id]
			GROUP BY sm.name
				,tb.name
				,co.system_type_id
				,co.max_length
			) C
		GROUP BY schm_name
			,table_name
		) B
	) A

order by est_mem_grant_MiB desc 

(457 rows affected)

Total execution time: 00:00:00.525

Table_name est_mem_grant_MiB dbo.ctasFixedMMP_BMCW 3488.00 dbo.ctasInputJoinKeyBM 3424.00 dbo.ctasInputJoinKey 3000.00 dbo.ctassupertablesum05132020 2760.00 ext.SuperTableSum20200414 2760.00 ext.SuperTableSum20200404 2752.00 dbo.ctassupertablesum 2752.00 ext.SuperTableStage2 2720.00 dbo.ctasSuperTableStage2 2712.00 dbo.HLRSegmentedPolicyRecords_Final2017Revised 2640.00 dbo.BrockSegmentedPolicyRecords_Final2017Revised 2640.00 dbo.SRUSSegmentedPolicyRecords_Final2017Revised 2640.00 dbo.MMP_sort_4Q18_AllTreaties 2616.00 dbo.ctasInputCleanBM_Prep3 2488.00 dbo.ctasInputCleanBM_Prep3Test 2488.00 dbo.ctasInputCleanBM_Prep3V2 2464.00 dbo.ctasInputCleanBM_Prep4 2464.00 dbo.ctasInputCleanBM_Prep4V2 2464.00 dbo.ctasInputCleanBM_Prep4V2Test 2464.00 dbo.ctasInputCleanBM 2464.00 dbo.ctasInputCleanBM_Prep2 2464.00 dbo.ctasInputCleanBM_Prep2V2 2464.00 dbo.ctasInputCleanBM_Prep1 2392.00 dbo.ctasInputCleanBM_Prep1V2 2392.00 dbo.BM_CW_RAMPs_FullStacked 2376.00 dbo.BM_CW_RAMPs_FullStacked_DupedGroupFix 2376.00 dbo.BM_CW_RAMPs_FullStacked_Old_NARDup 2376.00 dbo.ctasInputCleanBM_PrepBM 2368.00 dbo.vw_PLT_Use_Case 2256.00 dbo.ctasInputCleanxxx 1936.00 dbo.ctasInputClean 1936.00 dbo.Input12_B 1928.00 dbo.ctasInputClean_Prep 1888.00 dbo.input_12A 1784.00 dbo.Input12_BkUp 1768.00 dbo.Input12_Dev 1768.00 dbo.Input13 1768.00 dbo.ctasInput12Dirty 1768.00 dbo.Input12 1768.00 dbo.ctasCCIDMMPReplicate 1736.00 dbo.Input12_Test 1720.00 dbo.ctasPolMMPReplicate 1712.00 dbo.hashOrganicRAMP 1704.00 dbo.Organic_RAMPs_FullStacked 1704.00 dbo.Organic_mmp_4Q18Prod_ONB 1680.00 dbo.Organic_mmp 1640.00 dbo.BrockCAM_mmp_sji 1640.00 dbo.Input11 1632.00 dbo.test_RAMPs_bigmac_srt 1632.00 dbo.test_RAMPs_cwwithret_srt 1632.00 dbo.Test_RAMPsWithCorrectedDates 1608.00 dbo.Test_RAMPsWithCorrectedDates_v3 1608.00 dbo.BrockCAM_mmp_Stacked_DuplicateTape_Rerun 1608.00 dbo.BrockCAM_mmp_Stacked_MaxDateOnly 1608.00 dbo.BrockCAM_mmp_ked 1608.00 dbo.BrockCAM_mmp_ked_delete2 1608.00 dbo.Test_RAMPsWithCorrectedDates_v2 1592.00 dbo.ctasOutputStage3 1344.00 ext.ctasSuperTable 1336.00 dbo.MapCCIDModelFeatures 1336.00 dbo.jp_MAP_CCID_MODEL_FEATURES 1320.00 dbo.v5_MAP_CCID_MODEL_FEATURES 1320.00 dbo.v6_MAP_CCID_MODEL_FEATURES 1288.00 dbo.ctasSuperTableMap 1272.00 dbo.ctiiSuperTableMapMaxMask 1272.00 dbo.TreatyMap 1144.00 dbo.TreatyMap2 1144.00 dbo.mapTreatyReplicate 1144.00 ext.SuperTableStage 1136.00 dbo.ctasOutput12Stage2 1136.00 dbo.ctasOutput12Stage2TEST 1136.00 dbo.ctasOutput12Stage2xxx 1136.00 dbo.ctasSuperTableStage 1128.00 dbo.SAGEPrem 1056.00 dbo.HCF_Organic 1048.00 dbo.HCF_Brock 1032.00 dbo.ctasRolling12ReserveCalc 1008.00 dbo.ctasRolling36ReserveCalc 1008.00 dbo.Rates_IndustryQTables 976.00 dbo.Output12Stage2 976.00 dbo.Inforce12 848.00 dbo.ctasOutput12Stage 832.00 dbo.ctasOutputStage 832.00 dbo.Output12Stage 832.00 dbo.Temp_PowerBI_Testing_04_06_2019 824.00 dbo.ctasOutput12_Prep1 824.00 dbo.T_5360a8c0610142848e65d02db873bac1 808.00 dbo.T_a8e47c4c97f9414fb5673be090b15337 808.00 dbo.dev_SuperTable 792.00 dbo.futureProjectionOutputBMCW 784.00 dbo.Output12TEST 784.00 dbo.Output12_Prep2 768.00 dbo.Output12_Prep2TEST 768.00 dbo.ctasSeriatimDataWarehouseInforce 768.00 dbo.ctasOutput12_Prep2 768.00 dbo.BMCWseriatimTEST 760.00 dbo.Output12_ExtTEST 760.00 dbo.TempDeleteMe3bctas 752.00 dbo.Output12_working 744.00 dbo.ctasSeriatimDataWarehouseInforce_Prep 744.00 ext.TempDeleteMe3b 736.00 dbo.Output12BMCWxxx 728.00 dbo.Output12_Prep1 720.00 dbo.Output12_Prep1TEST 720.00 dbo.TempDeleteMe2b 720.00 dbo.Output12Prep2_stageRows 720.00 dbo.ctasOutput12_Prep2stageRows 720.00 dbo.ctasOutput12_Prep1TEST 720.00 dbo.Premium12 712.00 dbo.Premium12_old 712.00 ext.TempDeleteMe2b 704.00 dbo.TempDeleteMe2b_TEST 704.00 dbo.TempDeleteMe2c 704.00 ext.TempDeleteMe2c 688.00 dbo.Inforce12_A 688.00 dbo.ctasSeriatimDataWarehousePremium 680.00 dbo.ctasSuperInforce 672.00 dbo.ctasSuperTableSum1 672.00 dbo.TempDeleteMe2b_temp 672.00 dbo.TempDeleteMe2bshort 664.00 dbo.Output12TEST1 664.00 dbo.ctasSeriatimDataWarehousePremiu

## Rowgroup Details

In [5]:
SELECT	sm.[name]                                                       AS [logical_schema_name]
,       tb.[name]                                                       AS [logical_table_name]
,		ps.[distribution_id]                                            AS [distribution_id]
,		ps.[partition_number]
,		ps.[row_group_id]
,		ps.[delta_store_hobt_id]
,		ps.[state_desc]
,		ps.[total_rows]
,		ps.[deleted_rows]
,		ps.[size_in_bytes]
,		ps.[trim_reason_desc]
,		ps.[transition_to_compressed_state_desc]
,		ps.[has_vertipaq_optimization]
,		ps.[created_time]
,		ps.[closed_time]
,		ps.[generation]
FROM    sys.[schemas] sm
JOIN    sys.[tables] tb													ON  sm.[schema_id]          = tb.[schema_id]
JOIN    sys.[pdw_table_mappings] mp										ON  tb.[object_id]          = mp.[object_id]
JOIN    sys.[pdw_nodes_tables] nt										ON  nt.[name]               = mp.[physical_name]
JOIN	sys.[dm_pdw_nodes_db_column_store_row_group_physical_stats]	ps	ON  ps.[object_id]          = nt.[object_id]
																		AND ps.[pdw_node_id]        = nt.[pdw_node_id]
																		AND ps.[distribution_id]    = nt.[distribution_id]

(389287 rows affected)

Displaying Top 5000 rows.

Total execution time: 00:01:07.535

logical_schema_name logical_table_name distribution_id partition_number row_group_id delta_store_hobt_id state_desc total_rows deleted_rows size_in_bytes trim_reason_desc transition_to_compressed_state_desc has_vertipaq_optimization created_time closed_time generation dbo mapRptOnePostLevelJumpsCtasReplicate 1 1 0 72057594159562752 OPEN 41992 0 1957888 NULL NULL NULL 2019-07-30 09:55:07.170 NULL NULL dbo ctasReserveCleanCombosReplicate 2 1 0 72057594471776256 OPEN 18 0 16384 NULL NULL NULL 2020-02-25 18:17:18.543 NULL NULL dbo ctasRecoverCCIDMMPReplicate 3 1 6 NULL COMPRESSED 96645 0 1197232 REORG TUPLE_MOVER 1 2019-08-28 07:46:47.000 NULL 6 dbo Test_RAMPsWithCorrectedDates_v2 4 1 1 NULL COMPRESSED 69366 0 1582376 REORG TUPLE_MOVER 1 2019-06-07 23:21:11.053 2019-06-07 23:21:02.980 1 dbo CCID_OneMap_2_21_2019 5 1 0 72057594051887104 OPEN 1149 0 98304 NULL NULL NULL 2019-05-17 17:19:44.430 NULL NULL dbo test_RAMPs_cwwithret_srt 6 1 0 72057594051297280 OPEN 7160 0 4923392 NULL NULL NULL 2019-05-17 02:19:34.437 NULL NULL dbo vwGeneralLedger 7 1 0 72057594166444032 OPEN 1156 0 581632 NULL NULL NULL 2019-08-08 14:09:52.427 NULL NULL dbo Test_RAMPsWithCorrectedDates_v2 8 1 1 NULL COMPRESSED 69273 0 1889824 REORG TUPLE_MOVER 1 2019-06-07 23:22:24.903 2019-06-07 23:22:17.683 1 dbo Brock_Map_Recaptures 9 1 0 72057594139770880 OPEN 50 0 32768 NULL NULL NULL 2019-07-24 15:20:58.817 NULL NULL dbo ctasFixedMMP_BMCW 10 1 5 72057594654818304 OPEN 37058 0 50823168 NULL NULL NULL 2020-04-19 13:13:06.010 NULL NULL dbo IFRS_Factors_GAAP_ext_melt 11 1 1 NULL COMPRESSED 75980 0 675848 REORG TUPLE_MOVER 1 2019-10-14 18:34:24.607 2019-10-14 18:34:24.277 1 dbo BrockCAM_mmp_Stacked_DuplicateTape_Rerun 12 1 0 72057594239713280 OPEN 6647 0 5537792 NULL NULL NULL 2019-09-05 20:44:32.263 NULL NULL dbo PeoplSoftBrockReplicate 13 1 0 72057594113425408 OPEN 8 0 16384 NULL NULL NULL 2019-07-10 14:30:20.393 NULL NULL dbo jp_MAP_CCID_ACTUAL_FEATURES 14 1 5 NULL COMPRESSED 132045 0 2218636 REORG TUPLE_MOVER 1 2019-06-07 20:11:19.820 NULL 4 dbo ctasDropCombosJAMAS 15 1 0 72057594539147264 OPEN 9 0 16384 NULL NULL NULL 2020-02-29 01:59:25.483 NULL NULL dbo ctasOutput12FirstLastTapeSysJKND 16 1 9 NULL COMPRESSED 90801 0 490072 REORG TUPLE_MOVER 1 2020-05-31 02:50:58.460 NULL 8 dbo JAMAS_Data_Brock_v13b_NoFilter 17 1 0 NULL COMPRESSED 220752 0 11100830 BULKLOAD BULKLOAD 1 2019-09-18 21:38:00.580 NULL 1 dbo Output12_frExt 18 1 21 72057594696892416 OPEN 334 0 163840 NULL NULL NULL 2020-05-12 22:04:47.373 NULL NULL dbo ctasSuperTableSum1 19 1 112 72057594100776960 OPEN 19466 0 6365184 NULL NULL NULL 2019-07-02 17:19:10.477 NULL NULL dbo ctasOutputStageResTrueUp 20 1 0 72057594971488256 OPEN 20720 0 1515520 NULL NULL NULL 2020-06-01 12:35:10.757 NULL NULL dbo ctasInputCleanBM_Prep3 21 1 2 NULL COMPRESSED 158090 0 4936848 BULKLOAD BULKLOAD 1 2020-05-05 13:54:15.610 NULL 3 dbo ctasBMNovationFixCCIDStep1xxx 22 1 0 72057594674413568 OPEN 48394 0 5349376 NULL NULL NULL 2020-04-30 23:33:14.407 NULL NULL dbo JAMAS_Data_Brock_v13b_NoFilter 23 1 0 NULL COMPRESSED 220755 0 11097489 BULKLOAD BULKLOAD 1 2019-09-18 21:37:59.800 NULL 1 dbo ctasSuperMapPremiumJump 24 1 0 72057594177126400 OPEN 44707 0 2711552 NULL NULL NULL 2019-08-14 18:20:15.010 NULL NULL dbo PeopleSoftTreatyReplicate 25 1 0 72057594113228800 OPEN 4025 0 606208 NULL NULL NULL 2019-07-10 19:36:18.370 NULL NULL dbo IFRS_Factors_GAAP_ext_melt 26 1 1 NULL COMPRESSED 77290 0 663648 REORG TUPLE_MOVER 1 2019-10-14 18:34:21.893 2019-10-14 18:34:21.517 1 dbo Input11 27 1 4 NULL COMPRESSED 65620 0 2724032 REORG TUPLE_MOVER 1 2019-07-09 20:46:06.567 2019-07-09 20:46:00.207 4 dbo Output12Stage2 28 1 0 72057594902282240 OPEN 246 0 270336 NULL NULL NULL 2020-05-28 18:07:52.933 NULL NULL dbo ctasReserveCleanCombosReplicate 29 1 0 72057594491174912 OPEN 10 0 16384 NULL NULL NULL 2020-02-25 18:17:25.187 NULL NULL dbo CW_Term_Experience_Best_Estimate_deal_co_ser_term_rep_term 30 1 37 NULL COMPRESSED 57263 0 1642232 REORG TUPLE_MOVER 1

## Rowgroups

In [6]:
SELECT * 
	FROM 
	(SELECT	COUNT(*) AS Memory_Limitation
	FROM    sys.[schemas] sm
	JOIN    sys.[tables] tb													ON  sm.[schema_id]          = tb.[schema_id]
	JOIN    sys.[pdw_table_mappings] mp										ON  tb.[object_id]          = mp.[object_id]
	JOIN    sys.[pdw_nodes_tables] nt										ON  nt.[name]               = mp.[physical_name]
	JOIN	sys.[dm_pdw_nodes_db_column_store_row_group_physical_stats]	ps	ON  ps.[object_id]          = nt.[object_id]
																			AND ps.[pdw_node_id]        = nt.[pdw_node_id]
																			AND ps.[distribution_id]    = nt.[distribution_id]
	WHERE trim_reason_desc = 'MEMORY_LIMITATION') AS A, 
	(SELECT	COUNT(*) AS Bulkload
	FROM    sys.[schemas] sm
	JOIN    sys.[tables] tb													ON  sm.[schema_id]          = tb.[schema_id]
	JOIN    sys.[pdw_table_mappings] mp										ON  tb.[object_id]          = mp.[object_id]
	JOIN    sys.[pdw_nodes_tables] nt										ON  nt.[name]               = mp.[physical_name]
	JOIN	sys.[dm_pdw_nodes_db_column_store_row_group_physical_stats]	ps	ON  ps.[object_id]          = nt.[object_id]
																			AND ps.[pdw_node_id]        = nt.[pdw_node_id]
																			AND ps.[distribution_id]    = nt.[distribution_id]
	WHERE trim_reason_desc = 'BULKLOAD') AS B, 
	(SELECT	COUNT(*) AS Dictionary_Size
	FROM    sys.[schemas] sm
	JOIN    sys.[tables] tb													ON  sm.[schema_id]          = tb.[schema_id]
	JOIN    sys.[pdw_table_mappings] mp										ON  tb.[object_id]          = mp.[object_id]
	JOIN    sys.[pdw_nodes_tables] nt										ON  nt.[name]               = mp.[physical_name]
	JOIN	sys.[dm_pdw_nodes_db_column_store_row_group_physical_stats]	ps	ON  ps.[object_id]          = nt.[object_id]
																			AND ps.[pdw_node_id]        = nt.[pdw_node_id]
																			AND ps.[distribution_id]    = nt.[distribution_id]
	WHERE trim_reason_desc = 'DICTIONARY_SIZE') AS C

(1 row affected)

Total execution time: 00:00:04.433

Memory_Limitation Bulkload Dictionary_Size 21868 52289 217770

## Skew Detection

In [7]:
/* Returns the data distribution across all distribution databases to help detect any skew */
SELECT 
    distribution_id
,    SUM(reserved_space_GB)        as Data_Size_GB
FROM
(SELECT
   [execution_time]
,  [database_name]
,  [schema_name]
,  [table_name]
,  [two_part_name]
,  [node_table_name]
,  [node_table_name_seq]
,  [distribution_policy_name]
,  [distribution_column]
,  [distribution_id]
,  [index_type]
,  [index_type_desc]
,  [pdw_node_id]
,  [pdw_node_type]
,  [pdw_node_name]
,  [dist_name]
,  [dist_position]
,  [partition_nmbr]
,  [reserved_space_page_count]
,  [unused_space_page_count]
,  [data_space_page_count]
,  [index_space_page_count]
,  [row_count]
,  ([reserved_space_page_count] * 8.0)                                 AS [reserved_space_KB]
,  ([reserved_space_page_count] * 8.0)/1000                            AS [reserved_space_MB]
,  ([reserved_space_page_count] * 8.0)/1000000                         AS [reserved_space_GB]
,  ([reserved_space_page_count] * 8.0)/1000000000                      AS [reserved_space_TB]
,  ([unused_space_page_count]   * 8.0)                                 AS [unused_space_KB]
,  ([unused_space_page_count]   * 8.0)/1000                            AS [unused_space_MB]
,  ([unused_space_page_count]   * 8.0)/1000000                         AS [unused_space_GB]
,  ([unused_space_page_count]   * 8.0)/1000000000                      AS [unused_space_TB]
,  ([data_space_page_count]     * 8.0)                                 AS [data_space_KB]
,  ([data_space_page_count]     * 8.0)/1000                            AS [data_space_MB]
,  ([data_space_page_count]     * 8.0)/1000000                         AS [data_space_GB]
,  ([data_space_page_count]     * 8.0)/1000000000                      AS [data_space_TB]
,  ([index_space_page_count]  * 8.0)                                   AS [index_space_KB]
,  ([index_space_page_count]  * 8.0)/1000                              AS [index_space_MB]
,  ([index_space_page_count]  * 8.0)/1000000                           AS [index_space_GB]
,  ([index_space_page_count]  * 8.0)/1000000000                        AS [index_space_TB]
FROM
	(SELECT 
	 GETDATE()                                                             AS  [execution_time]
	, DB_NAME()                                                            AS  [database_name]
	, s.name                                                               AS  [schema_name]
	, t.name                                                               AS  [table_name]
	, QUOTENAME(s.name)+'.'+QUOTENAME(t.name)                              AS  [two_part_name]
	, nt.[name]                                                            AS  [node_table_name]
	, ROW_NUMBER() OVER(PARTITION BY nt.[name] ORDER BY (SELECT NULL))     AS  [node_table_name_seq]
	, tp.[distribution_policy_desc]                                        AS  [distribution_policy_name]
	, c.[name]                                                             AS  [distribution_column]
	, nt.[distribution_id]                                                 AS  [distribution_id]
	, i.[type]                                                             AS  [index_type]
	, i.[type_desc]                                                        AS  [index_type_desc]
	, nt.[pdw_node_id]                                                     AS  [pdw_node_id]
	, pn.[type]                                                            AS  [pdw_node_type]
	, pn.[name]                                                            AS  [pdw_node_name]
	, di.name                                                              AS  [dist_name]
	, di.position                                                          AS  [dist_position]
	, nps.[partition_number]                                               AS  [partition_nmbr]
	, nps.[reserved_page_count]                                            AS  [reserved_space_page_count]
	, nps.[reserved_page_count] - nps.[used_page_count]                    AS  [unused_space_page_count]
	, nps.[in_row_data_page_count] 
		+ nps.[row_overflow_used_page_count] 
		+ nps.[lob_used_page_count]                                        AS  [data_space_page_count]
	, nps.[reserved_page_count] 
	 - (nps.[reserved_page_count] - nps.[used_page_count]) 
	 - ([in_row_data_page_count] 
			 + [row_overflow_used_page_count]+[lob_used_page_count])       AS  [index_space_page_count]
	, nps.[row_count]                                                      AS  [row_count]
	from 
		sys.schemas s
	INNER JOIN sys.tables t
		ON s.[schema_id] = t.[schema_id]
	INNER JOIN sys.indexes i
		ON  t.[object_id] = i.[object_id]
		AND i.[index_id] <= 1
	INNER JOIN sys.pdw_table_distribution_properties tp
		ON t.[object_id] = tp.[object_id]
	INNER JOIN sys.pdw_table_mappings tm
		ON t.[object_id] = tm.[object_id]
	INNER JOIN sys.pdw_nodes_tables nt
		ON tm.[physical_name] = nt.[name]
	INNER JOIN sys.dm_pdw_nodes pn
		ON  nt.[pdw_node_id] = pn.[pdw_node_id]
	INNER JOIN sys.pdw_distributions di
		ON  nt.[distribution_id] = di.[distribution_id]
	INNER JOIN sys.dm_pdw_nodes_db_partition_stats nps
		ON nt.[object_id] = nps.[object_id]
		AND nt.[pdw_node_id] = nps.[pdw_node_id]
		AND nt.[distribution_id] = nps.[distribution_id]
	LEFT OUTER JOIN (select * from sys.pdw_column_distribution_properties where distribution_ordinal = 1) cdp
		ON t.[object_id] = cdp.[object_id]
	LEFT OUTER JOIN sys.columns c
		ON cdp.[object_id] = c.[object_id]
		AND cdp.[column_id] = c.[column_id]) AS Base) AS Base1
GROUP BY     distribution_id

(60 rows affected)

Total execution time: 00:00:04.816

distribution_id Data_Size_GB 1 219.843072000 2 216.426232000 3 216.719784000 4 217.335528000 5 216.845168000 6 218.407696000 7 216.491080000 8 217.234488000 9 216.759848000 10 217.436472000 11 216.819704000 12 217.261752000 13 216.226952000 14 216.699120000 15 217.190096000 16 216.982968000 17 217.628024000 18 216.672048000 19 216.920296000 20 216.357712000 21 222.161616000 22 217.192960000 23 217.682312000 24 217.365480000 25 217.613200000 26 217.468736000 27 216.636352000 28 217.415152000 29 217.271200000 30 216.934416000 31 217.895736000 32 216.997328000 33 216.848520000 34 217.126088000 35 217.428536000 36 216.593448000 37 218.337080000 38 216.574320000 39 216.386560000 40 216.482408000 41 217.120600000 42 216.625808000 43 217.541728000 44 216.153560000 45 217.356448000 46 217.060592000 47 217.203272000 48 217.593496000 49 216.628552000 50 217.889344000 51 216.903208000 52 217.837328000 53 268.663728000 54 217.670992000 55 217.319696000 56 218.038232000 57 216.035296000 58 216.889800000 59 218.162680000 60 216.609144000

## Slot Usage

In [8]:
-- Total running queries and slots consumed
SELECT
	SUM(CASE WHEN r.[status] ='Running'   THEN 1 ELSE 0 END)							[running_queries]
	, SUM(CASE WHEN r.[status] ='Running'   THEN rw.concurrency_slots_used ELSE 0 END)	[running_queries_slots]
	, SUM(CASE WHEN r.[status] ='Suspended' THEN 1 ELSE 0 END)							[queued_queries]
	, SUM(CASE WHEN rw.[state] ='Queued'    THEN rw.concurrency_slots_used ELSE 0 END)	[queued_queries_slots]
FROM
	[sys].[dm_pdw_exec_requests] r 
	JOIN [sys].[dm_pdw_resource_waits] rw ON rw.request_id = r.request_id
WHERE
	( (r.[status] = 'Running' AND r.[resource_class] IS NOT NULL ) OR r.[status] ='Suspended' )
	AND rw.[type] ='UserConcurrencyResourceType';

(1 row affected)

Total execution time: 00:00:00.269

running_queries running_queries_slots queued_queries queued_queries_slots NULL NULL NULL NULL

## Storage Size

In [9]:
/* Returns reserved space within the database broken down into the data, index, and unused space */
SELECT 'data_space_GB', sum(data_space_GB) AS data_space_GB
    FROM
    (SELECT
    [execution_time]
    ,  [database_name]
    ,  [schema_name]
    ,  [table_name]
    ,  [two_part_name]
    ,  [node_table_name]
    ,  [node_table_name_seq]
    ,  [distribution_policy_name]
    ,  [distribution_column]
    ,  [distribution_id]
    ,  [index_type]
    ,  [index_type_desc]
    ,  [pdw_node_id]
    ,  [pdw_node_type]
    ,  [pdw_node_name]
    ,  [dist_name]
    ,  [dist_position]
    ,  [partition_nmbr]
    ,  [reserved_space_page_count]
    ,  [unused_space_page_count]
    ,  [data_space_page_count]
    ,  [index_space_page_count]
    ,  [row_count]
    ,  ([reserved_space_page_count] * 8.0)                                 AS [reserved_space_KB]
    ,  ([reserved_space_page_count] * 8.0)/1000                            AS [reserved_space_MB]
    ,  ([reserved_space_page_count] * 8.0)/1000000                         AS [reserved_space_GB]
    ,  ([reserved_space_page_count] * 8.0)/1000000000                      AS [reserved_space_TB]
    ,  ([unused_space_page_count]   * 8.0)                                 AS [unused_space_KB]
    ,  ([unused_space_page_count]   * 8.0)/1000                            AS [unused_space_MB]
    ,  ([unused_space_page_count]   * 8.0)/1000000                         AS [unused_space_GB]
    ,  ([unused_space_page_count]   * 8.0)/1000000000                      AS [unused_space_TB]
    ,  ([data_space_page_count]     * 8.0)                                 AS [data_space_KB]
    ,  ([data_space_page_count]     * 8.0)/1000                            AS [data_space_MB]
    ,  ([data_space_page_count]     * 8.0)/1000000                         AS [data_space_GB]
    ,  ([data_space_page_count]     * 8.0)/1000000000                      AS [data_space_TB]
    ,  ([index_space_page_count]  * 8.0)                                   AS [index_space_KB]
    ,  ([index_space_page_count]  * 8.0)/1000                              AS [index_space_MB]
    ,  ([index_space_page_count]  * 8.0)/1000000                           AS [index_space_GB]
    ,  ([index_space_page_count]  * 8.0)/1000000000                        AS [index_space_TB]
    FROM
        (SELECT 
        GETDATE()                                                             AS  [execution_time]
        , DB_NAME()                                                            AS  [database_name]
        , s.name                                                               AS  [schema_name]
        , t.name                                                               AS  [table_name]
        , QUOTENAME(s.name)+'.'+QUOTENAME(t.name)                              AS  [two_part_name]
        , nt.[name]                                                            AS  [node_table_name]
        , ROW_NUMBER() OVER(PARTITION BY nt.[name] ORDER BY (SELECT NULL))     AS  [node_table_name_seq]
        , tp.[distribution_policy_desc]                                        AS  [distribution_policy_name]
        , c.[name]                                                             AS  [distribution_column]
        , nt.[distribution_id]                                                 AS  [distribution_id]
        , i.[type]                                                             AS  [index_type]
        , i.[type_desc]                                                        AS  [index_type_desc]
        , nt.[pdw_node_id]                                                     AS  [pdw_node_id]
        , pn.[type]                                                            AS  [pdw_node_type]
        , pn.[name]                                                            AS  [pdw_node_name]
        , di.name                                                              AS  [dist_name]
        , di.position                                                          AS  [dist_position]
        , nps.[partition_number]                                               AS  [partition_nmbr]
        , nps.[reserved_page_count]                                            AS  [reserved_space_page_count]
        , nps.[reserved_page_count] - nps.[used_page_count]                    AS  [unused_space_page_count]
        , nps.[in_row_data_page_count] 
            + nps.[row_overflow_used_page_count] 
            + nps.[lob_used_page_count]                                        AS  [data_space_page_count]
        , nps.[reserved_page_count] 
        - (nps.[reserved_page_count] - nps.[used_page_count]) 
        - ([in_row_data_page_count] 
                + [row_overflow_used_page_count]+[lob_used_page_count])       AS  [index_space_page_count]
        , nps.[row_count]                                                      AS  [row_count]
        from 
            sys.schemas s
        INNER JOIN sys.tables t
            ON s.[schema_id] = t.[schema_id]
        INNER JOIN sys.indexes i
            ON  t.[object_id] = i.[object_id]
            AND i.[index_id] <= 1
        INNER JOIN sys.pdw_table_distribution_properties tp
            ON t.[object_id] = tp.[object_id]
        INNER JOIN sys.pdw_table_mappings tm
            ON t.[object_id] = tm.[object_id]
        INNER JOIN sys.pdw_nodes_tables nt
            ON tm.[physical_name] = nt.[name]
        INNER JOIN sys.dm_pdw_nodes pn
            ON  nt.[pdw_node_id] = pn.[pdw_node_id]
        INNER JOIN sys.pdw_distributions di
            ON  nt.[distribution_id] = di.[distribution_id]
        INNER JOIN sys.dm_pdw_nodes_db_partition_stats nps
            ON nt.[object_id] = nps.[object_id]
            AND nt.[pdw_node_id] = nps.[pdw_node_id]
            AND nt.[distribution_id] = nps.[distribution_id]
        LEFT OUTER JOIN (select * from sys.pdw_column_distribution_properties where distribution_ordinal = 1) cdp
            ON t.[object_id] = cdp.[object_id]
        LEFT OUTER JOIN sys.columns c
            ON cdp.[object_id] = c.[object_id]
            AND cdp.[column_id] = c.[column_id]) AS Base) AS Base1
UNION ALL
SELECT 'index_space_GB', sum(index_space_GB) AS index_space_GB
    FROM
    (SELECT
    [execution_time]
    ,  [database_name]
    ,  [schema_name]
    ,  [table_name]
    ,  [two_part_name]
    ,  [node_table_name]
    ,  [node_table_name_seq]
    ,  [distribution_policy_name]
    ,  [distribution_column]
    ,  [distribution_id]
    ,  [index_type]
    ,  [index_type_desc]
    ,  [pdw_node_id]
    ,  [pdw_node_type]
    ,  [pdw_node_name]
    ,  [dist_name]
    ,  [dist_position]
    ,  [partition_nmbr]
    ,  [reserved_space_page_count]
    ,  [unused_space_page_count]
    ,  [data_space_page_count]
    ,  [index_space_page_count]
    ,  [row_count]
    ,  ([reserved_space_page_count] * 8.0)                                 AS [reserved_space_KB]
    ,  ([reserved_space_page_count] * 8.0)/1000                            AS [reserved_space_MB]
    ,  ([reserved_space_page_count] * 8.0)/1000000                         AS [reserved_space_GB]
    ,  ([reserved_space_page_count] * 8.0)/1000000000                      AS [reserved_space_TB]
    ,  ([unused_space_page_count]   * 8.0)                                 AS [unused_space_KB]
    ,  ([unused_space_page_count]   * 8.0)/1000                            AS [unused_space_MB]
    ,  ([unused_space_page_count]   * 8.0)/1000000                         AS [unused_space_GB]
    ,  ([unused_space_page_count]   * 8.0)/1000000000                      AS [unused_space_TB]
    ,  ([data_space_page_count]     * 8.0)                                 AS [data_space_KB]
    ,  ([data_space_page_count]     * 8.0)/1000                            AS [data_space_MB]
    ,  ([data_space_page_count]     * 8.0)/1000000                         AS [data_space_GB]
    ,  ([data_space_page_count]     * 8.0)/1000000000                      AS [data_space_TB]
    ,  ([index_space_page_count]  * 8.0)                                   AS [index_space_KB]
    ,  ([index_space_page_count]  * 8.0)/1000                              AS [index_space_MB]
    ,  ([index_space_page_count]  * 8.0)/1000000                           AS [index_space_GB]
    ,  ([index_space_page_count]  * 8.0)/1000000000                        AS [index_space_TB]
    FROM
        (SELECT 
        GETDATE()                                                             AS  [execution_time]
        , DB_NAME()                                                            AS  [database_name]
        , s.name                                                               AS  [schema_name]
        , t.name                                                               AS  [table_name]
        , QUOTENAME(s.name)+'.'+QUOTENAME(t.name)                              AS  [two_part_name]
        , nt.[name]                                                            AS  [node_table_name]
        , ROW_NUMBER() OVER(PARTITION BY nt.[name] ORDER BY (SELECT NULL))     AS  [node_table_name_seq]
        , tp.[distribution_policy_desc]                                        AS  [distribution_policy_name]
        , c.[name]                                                             AS  [distribution_column]
        , nt.[distribution_id]                                                 AS  [distribution_id]
        , i.[type]                                                             AS  [index_type]
        , i.[type_desc]                                                        AS  [index_type_desc]
        , nt.[pdw_node_id]                                                     AS  [pdw_node_id]
        , pn.[type]                                                            AS  [pdw_node_type]
        , pn.[name]                                                            AS  [pdw_node_name]
        , di.name                                                              AS  [dist_name]
        , di.position                                                          AS  [dist_position]
        , nps.[partition_number]                                               AS  [partition_nmbr]
        , nps.[reserved_page_count]                                            AS  [reserved_space_page_count]
        , nps.[reserved_page_count] - nps.[used_page_count]                    AS  [unused_space_page_count]
        , nps.[in_row_data_page_count] 
            + nps.[row_overflow_used_page_count] 
            + nps.[lob_used_page_count]                                        AS  [data_space_page_count]
        , nps.[reserved_page_count] 
        - (nps.[reserved_page_count] - nps.[used_page_count]) 
        - ([in_row_data_page_count] 
                + [row_overflow_used_page_count]+[lob_used_page_count])       AS  [index_space_page_count]
        , nps.[row_count]                                                      AS  [row_count]
        from 
            sys.schemas s
        INNER JOIN sys.tables t
            ON s.[schema_id] = t.[schema_id]
        INNER JOIN sys.indexes i
            ON  t.[object_id] = i.[object_id]
            AND i.[index_id] <= 1
        INNER JOIN sys.pdw_table_distribution_properties tp
            ON t.[object_id] = tp.[object_id]
        INNER JOIN sys.pdw_table_mappings tm
            ON t.[object_id] = tm.[object_id]
        INNER JOIN sys.pdw_nodes_tables nt
            ON tm.[physical_name] = nt.[name]
        INNER JOIN sys.dm_pdw_nodes pn
            ON  nt.[pdw_node_id] = pn.[pdw_node_id]
        INNER JOIN sys.pdw_distributions di
            ON  nt.[distribution_id] = di.[distribution_id]
        INNER JOIN sys.dm_pdw_nodes_db_partition_stats nps
            ON nt.[object_id] = nps.[object_id]
            AND nt.[pdw_node_id] = nps.[pdw_node_id]
            AND nt.[distribution_id] = nps.[distribution_id]
        LEFT OUTER JOIN (select * from sys.pdw_column_distribution_properties where distribution_ordinal = 1) cdp
            ON t.[object_id] = cdp.[object_id]
        LEFT OUTER JOIN sys.columns c
            ON cdp.[object_id] = c.[object_id]
            AND cdp.[column_id] = c.[column_id]) AS Base) AS Base1
UNION ALL
SELECT 'unused_space_GB', sum(unused_space_GB) AS unused_space_GB
    FROM
    (SELECT
    [execution_time]
    ,  [database_name]
    ,  [schema_name]
    ,  [table_name]
    ,  [two_part_name]
    ,  [node_table_name]
    ,  [node_table_name_seq]
    ,  [distribution_policy_name]
    ,  [distribution_column]
    ,  [distribution_id]
    ,  [index_type]
    ,  [index_type_desc]
    ,  [pdw_node_id]
    ,  [pdw_node_type]
    ,  [pdw_node_name]
    ,  [dist_name]
    ,  [dist_position]
    ,  [partition_nmbr]
    ,  [reserved_space_page_count]
    ,  [unused_space_page_count]
    ,  [data_space_page_count]
    ,  [index_space_page_count]
    ,  [row_count]
    ,  ([reserved_space_page_count] * 8.0)                                 AS [reserved_space_KB]
    ,  ([reserved_space_page_count] * 8.0)/1000                            AS [reserved_space_MB]
    ,  ([reserved_space_page_count] * 8.0)/1000000                         AS [reserved_space_GB]
    ,  ([reserved_space_page_count] * 8.0)/1000000000                      AS [reserved_space_TB]
    ,  ([unused_space_page_count]   * 8.0)                                 AS [unused_space_KB]
    ,  ([unused_space_page_count]   * 8.0)/1000                            AS [unused_space_MB]
    ,  ([unused_space_page_count]   * 8.0)/1000000                         AS [unused_space_GB]
    ,  ([unused_space_page_count]   * 8.0)/1000000000                      AS [unused_space_TB]
    ,  ([data_space_page_count]     * 8.0)                                 AS [data_space_KB]
    ,  ([data_space_page_count]     * 8.0)/1000                            AS [data_space_MB]
    ,  ([data_space_page_count]     * 8.0)/1000000                         AS [data_space_GB]
    ,  ([data_space_page_count]     * 8.0)/1000000000                      AS [data_space_TB]
    ,  ([index_space_page_count]  * 8.0)                                   AS [index_space_KB]
    ,  ([index_space_page_count]  * 8.0)/1000                              AS [index_space_MB]
    ,  ([index_space_page_count]  * 8.0)/1000000                           AS [index_space_GB]
    ,  ([index_space_page_count]  * 8.0)/1000000000                        AS [index_space_TB]
    FROM
        (SELECT 
        GETDATE()                                                             AS  [execution_time]
        , DB_NAME()                                                            AS  [database_name]
        , s.name                                                               AS  [schema_name]
        , t.name                                                               AS  [table_name]
        , QUOTENAME(s.name)+'.'+QUOTENAME(t.name)                              AS  [two_part_name]
        , nt.[name]                                                            AS  [node_table_name]
        , ROW_NUMBER() OVER(PARTITION BY nt.[name] ORDER BY (SELECT NULL))     AS  [node_table_name_seq]
        , tp.[distribution_policy_desc]                                        AS  [distribution_policy_name]
        , c.[name]                                                             AS  [distribution_column]
        , nt.[distribution_id]                                                 AS  [distribution_id]
        , i.[type]                                                             AS  [index_type]
        , i.[type_desc]                                                        AS  [index_type_desc]
        , nt.[pdw_node_id]                                                     AS  [pdw_node_id]
        , pn.[type]                                                            AS  [pdw_node_type]
        , pn.[name]                                                            AS  [pdw_node_name]
        , di.name                                                              AS  [dist_name]
        , di.position                                                          AS  [dist_position]
        , nps.[partition_number]                                               AS  [partition_nmbr]
        , nps.[reserved_page_count]                                            AS  [reserved_space_page_count]
        , nps.[reserved_page_count] - nps.[used_page_count]                    AS  [unused_space_page_count]
        , nps.[in_row_data_page_count] 
            + nps.[row_overflow_used_page_count] 
            + nps.[lob_used_page_count]                                        AS  [data_space_page_count]
        , nps.[reserved_page_count] 
        - (nps.[reserved_page_count] - nps.[used_page_count]) 
        - ([in_row_data_page_count] 
                + [row_overflow_used_page_count]+[lob_used_page_count])       AS  [index_space_page_count]
        , nps.[row_count]                                                      AS  [row_count]
        from 
            sys.schemas s
        INNER JOIN sys.tables t
            ON s.[schema_id] = t.[schema_id]
        INNER JOIN sys.indexes i
            ON  t.[object_id] = i.[object_id]
            AND i.[index_id] <= 1
        INNER JOIN sys.pdw_table_distribution_properties tp
            ON t.[object_id] = tp.[object_id]
        INNER JOIN sys.pdw_table_mappings tm
            ON t.[object_id] = tm.[object_id]
        INNER JOIN sys.pdw_nodes_tables nt
            ON tm.[physical_name] = nt.[name]
        INNER JOIN sys.dm_pdw_nodes pn
            ON  nt.[pdw_node_id] = pn.[pdw_node_id]
        INNER JOIN sys.pdw_distributions di
            ON  nt.[distribution_id] = di.[distribution_id]
        INNER JOIN sys.dm_pdw_nodes_db_partition_stats nps
            ON nt.[object_id] = nps.[object_id]
            AND nt.[pdw_node_id] = nps.[pdw_node_id]
            AND nt.[distribution_id] = nps.[distribution_id]
        LEFT OUTER JOIN (select * from sys.pdw_column_distribution_properties where distribution_ordinal = 1) cdp
            ON t.[object_id] = cdp.[object_id]
        LEFT OUTER JOIN sys.columns c
            ON cdp.[object_id] = c.[object_id]
            AND cdp.[column_id] = c.[column_id]) AS Base) AS Base1

(3 rows affected)

Total execution time: 00:00:14.318

(No column name) data_space_GB data_space_GB 13082.255760000 index_space_GB 0.456592000 unused_space_GB 3.260640000

## Table Health Count

In [10]:
/* Retuns the number of tables which may be suffering from poor quality segments */

Select * FROM 
(
    SELECT    Count(*) AS Poor_Quality_Segments
    FROM
        (SELECT
        GETDATE()                                                               AS [execution_date]
,       DB_Name()                                                               AS [database_name]
,       s.name                                                                  AS [schema_name]
,       t.name                                                                  AS [table_name]
,    COUNT(DISTINCT rg.[partition_number])                    AS [table_partition_count]
,       SUM(rg.[total_rows])                                                    AS [row_count_total]
,       SUM(rg.[total_rows])/COUNT(DISTINCT rg.[distribution_id])               AS [row_count_per_distribution_MAX]
,    CEILING    ((SUM(rg.[total_rows])*1.0/COUNT(DISTINCT rg.[distribution_id]))/1048576) AS [rowgroup_per_distribution_MAX]
,       SUM(CASE WHEN rg.[State] = 0 THEN 1                   ELSE 0    END)    AS [INVISIBLE_rowgroup_count]
,       SUM(CASE WHEN rg.[State] = 0 THEN rg.[total_rows]     ELSE 0    END)    AS [INVISIBLE_rowgroup_rows]
,       MIN(CASE WHEN rg.[State] = 0 THEN rg.[total_rows]     ELSE NULL END)    AS [INVISIBLE_rowgroup_rows_MIN]
,       MAX(CASE WHEN rg.[State] = 0 THEN rg.[total_rows]     ELSE NULL END)    AS [INVISIBLE_rowgroup_rows_MAX]
,       AVG(CASE WHEN rg.[State] = 0 THEN rg.[total_rows]     ELSE NULL END)    AS [INVISIBLE_rowgroup_rows_AVG]
,       SUM(CASE WHEN rg.[State] = 1 THEN 1                   ELSE 0    END)    AS [OPEN_rowgroup_count]
,       SUM(CASE WHEN rg.[State] = 1 THEN rg.[total_rows]     ELSE 0    END)    AS [OPEN_rowgroup_rows]
,       MIN(CASE WHEN rg.[State] = 1 THEN rg.[total_rows]     ELSE NULL END)    AS [OPEN_rowgroup_rows_MIN]
,       MAX(CASE WHEN rg.[State] = 1 THEN rg.[total_rows]     ELSE NULL END)    AS [OPEN_rowgroup_rows_MAX]
,       AVG(CASE WHEN rg.[State] = 1 THEN rg.[total_rows]     ELSE NULL END)    AS [OPEN_rowgroup_rows_AVG]
,       SUM(CASE WHEN rg.[State] = 2 THEN 1                   ELSE 0    END)    AS [CLOSED_rowgroup_count]
,       SUM(CASE WHEN rg.[State] = 2 THEN rg.[total_rows]     ELSE 0    END)    AS [CLOSED_rowgroup_rows]
,       MIN(CASE WHEN rg.[State] = 2 THEN rg.[total_rows]     ELSE NULL END)    AS [CLOSED_rowgroup_rows_MIN]
,       MAX(CASE WHEN rg.[State] = 2 THEN rg.[total_rows]     ELSE NULL END)    AS [CLOSED_rowgroup_rows_MAX]
,       AVG(CASE WHEN rg.[State] = 2 THEN rg.[total_rows]     ELSE NULL END)    AS [CLOSED_rowgroup_rows_AVG]
,       SUM(CASE WHEN rg.[State] = 3 THEN 1                   ELSE 0    END)    AS [COMPRESSED_rowgroup_count]
,       SUM(CASE WHEN rg.[State] = 3 THEN rg.[total_rows]     ELSE 0    END)    AS [COMPRESSED_rowgroup_rows]
,       SUM(CASE WHEN rg.[State] = 3 THEN rg.[deleted_rows]   ELSE 0    END)    AS [COMPRESSED_rowgroup_rows_DELETED]
,       MIN(CASE WHEN rg.[State] = 3 THEN rg.[total_rows]     ELSE NULL END)    AS [COMPRESSED_rowgroup_rows_MIN]
,       MAX(CASE WHEN rg.[State] = 3 THEN rg.[total_rows]     ELSE NULL END)    AS [COMPRESSED_rowgroup_rows_MAX]
,       AVG(CASE WHEN rg.[State] = 3 THEN rg.[total_rows]     ELSE NULL END)    AS [COMPRESSED_rowgroup_rows_AVG]
,       'ALTER INDEX ALL ON ' + s.name + '.' + t.NAME + ' REBUILD;'             AS [Rebuild_Index_SQL]
FROM    sys.[pdw_nodes_column_store_row_groups] rg
JOIN    sys.[pdw_nodes_tables] nt                   ON  rg.[object_id]          = nt.[object_id]
                                                    AND rg.[pdw_node_id]        = nt.[pdw_node_id]
                                                    AND rg.[distribution_id]    = nt.[distribution_id]
JOIN    sys.[pdw_table_mappings] mp                 ON  nt.[name]               = mp.[physical_name]
JOIN    sys.[tables] t                              ON  mp.[object_id]          = t.[object_id]
JOIN    sys.[schemas] s                             ON t.[schema_id]            = s.[schema_id]
GROUP BY
        s.[name]
,       t.[name]) AS segmentQuality
    WHERE    COMPRESSED_rowgroup_rows_AVG < 100000
            OR INVISIBLE_rowgroup_rows_AVG < 100000
) A, 
(
SELECT
    COUNT(*) AS Stale_Stats_7_Days
FROM
    sys.objects ob
    JOIN sys.stats st
        ON  ob.[object_id] = st.[object_id]
    JOIN sys.stats_columns sc    
        ON  st.[stats_id] = sc.[stats_id]
        AND st.[object_id] = sc.[object_id]
    JOIN sys.columns co    
        ON  sc.[column_id] = co.[column_id]
        AND sc.[object_id] = co.[object_id]
    JOIN sys.types  ty    
        ON  co.[user_type_id] = ty.[user_type_id]
    JOIN sys.tables tb    
        ON  co.[object_id] = tb.[object_id]
    JOIN sys.schemas sm    
        ON  tb.[schema_id] = sm.[schema_id]
WHERE
    st.[user_created] = 1
AND STATS_DATE(st.[object_id],st.[stats_id]) < dateadd(day,-7,getdate())) B

(1 row affected)

Total execution time: 00:00:04.671

Poor_Quality_Segments Stale_Stats_7_Days 28 0

## Tempdb Consumption

In [11]:
/* Monitor tempdb per compute node */
SELECT
    ssu.pdw_node_id,
    (SUM((ssu.user_objects_alloc_page_count * 8)) + SUM((ssu.internal_objects_alloc_page_count * 8))) AS 'Tempdb_Space_Allocated_KB'
FROM sys.dm_pdw_nodes_db_session_space_usage AS ssu
WHERE DB_NAME(ssu.database_id) = 'tempdb'
GROUP BY ssu.pdw_node_id

(16 rows affected)

Total execution time: 00:00:00.580

pdw_node_id Tempdb_Space_Allocated_KB 1 1152 6 384 8 384 10 192 23 256 24 384 37 440783616 38 384 42 1856 48 448 49 320 53 320 54 1024 55 1024 56 1216 58 390336

## User Activites

In [13]:
/* Monitor active sessions, queries, and queried queries */
SELECT * FROM
(
    -- Active Sessions
    SELECT COUNT(*) AS Active_Sessions
    FROM sys.dm_pdw_exec_sessions 
    WHERE status <> 'Closed' and session_id <> session_id()
) A, 
(
    -- Active Queries
    SELECT COUNT(*) AS Active_Queries
    FROM sys.dm_pdw_exec_requests 
    WHERE status not in ('Completed','Failed','Cancelled')
    AND session_id <> session_id()
) B,
(-- Waiting Queued queries
    SELECT COUNT(*) AS Queued_Queries
    FROM   sys.dm_pdw_waits waits
    JOIN  sys.dm_pdw_exec_requests requests
    ON waits.request_id=requests.request_id
    WHERE status <> 'Closed' and waits.session_id <> session_id() and waits.state = 'AcquireResources'
) C,
(-- Waiting load queries
    SELECT Count(*) AS Loads
    FROM
       sys.dm_pdw_dms_external_work s INNER JOIN 
    sys.dm_pdw_exec_requests r
        ON r.request_id = s.request_id
    --WHERE command IN('%CREATE TABLE AS%', '%INSERT%') AND r.status = 'Running' 
) D

(1 row affected)

Total execution time: 00:00:00.603

Active_Sessions Active_Queries Queued_Queries Loads 13 16 0 0

## User Activities Details

In [18]:
SELECT *
FROM sys.dm_pdw_exec_sessions 
WHERE status ='active' 
and session_id <> session_id()

(3 rows affected)

Total execution time: 00:00:00.223

session_id status request_id security_id login_name login_time query_count is_transactional client_id app_name sql_spid SID380101 Active QID3187802 NULL LoaderXL 2020-06-01 12:36:45.507 8 0 20.41.3.4:8832 AzureDataMovement 914 SID380755 Active QID3196881 NULL analytics_admins 2020-06-01 20:30:39.593 41 0 4.78.43.62:3609 azdata-languageService 92 SID380126 Active QID3188082 NULL LoaderXL 2020-06-01 13:26:32.123 8 0 20.41.3.4:13888 AzureDataMovement 97